In [ ]:
# !pip install pandas 
# !pip install googletrans==4.0.0-rc1
# ! pip install deep-translator

In [ ]:
import pandas as pd

# โหลดข้อมูลจากไฟล์ CSV
df = pd.read_csv('dataset/dataset.csv')

# ตรวจสอบข้อมูลเบื้องต้น
# print(df.head())
print(df['label'].value_counts())

label
minimum     2587
moderate     394
mild         290
severe       282
Name: count, dtype: int64


Data Augmentation(Back Translation)

In [ ]:
from deep_translator import GoogleTranslator
import pandas as pd

# ฟังก์ชันสำหรับ Back Translation โดยใช้ภาษาไทยเป็นภาษากลาง
def back_translate(text, src='en', mid='th'):
    try:
        print(f"Original: {text}")  # แสดงข้อความก่อนแปล
        translated = GoogleTranslator(source=src, target=mid).translate(text)  # แปลเป็นภาษาไทย
        print(f"Translated to Thai: {translated}")  # แสดงข้อความหลังแปลเป็นไทย
        back_translated = GoogleTranslator(source=mid, target=src).translate(translated)  # แปลกลับเป็นอังกฤษ
        print(f"Back Translated to English: {back_translated}\n")  # แสดงข้อความหลังแปลกลับ
        return back_translated
    except Exception as e:
        print(f"Error translating: {e}")
        return text  # ถ้าแปลไม่ได้ให้คืนค่าเดิม

# โหลดข้อมูล
print("Loading dataset...")
df = pd.read_csv('dataset/dataset.csv')
print(f"Dataset loaded: {df.shape[0]} rows\n")

# เลือกเฉพาะ class ที่มีน้อย (mild, moderate, severe) มาเพิ่มข้อมูล
print("Filtering underrepresented classes (mild, moderate, severe)...")
df_aug = df[df['label'].isin(['mild', 'moderate', 'severe'])].copy()
print(f"Selected {df_aug.shape[0]} rows for augmentation\n")

# ใช้ Back Translation
print("Applying Back Translation...")
df_aug['text'] = df_aug['text'].apply(lambda x: back_translate(x))

# รวมข้อมูลใหม่กับข้อมูลเดิม
df = pd.concat([df, df_aug])
print(f"New dataset size after augmentation: {df.shape[0]} rows\n")

# บันทึกข้อมูลที่เพิ่มแล้ว
output_file = 'dataset_augmented.csv'
df.to_csv(output_file, index=False)
print(f"Augmented dataset saved as {output_file}")


Loading dataset...
Dataset loaded: 3553 rows

Filtering underrepresented classes (mild, moderate, severe)...
Selected 966 rows for augmentation

Applying Back Translation...
Original: He said he had not felt that way before, suggeted I go rest and so ..TRIGGER AHEAD IF YOUI'RE A HYPOCONDRIAC LIKE ME: i decide to look up "feelings of doom" in hopes of maybe getting sucked into some rabbit hole of ludicrous conspiracy, a stupid "are you psychic" test or new age b.s., something I could even laugh at down the road. No, I ended up reading that this sense of doom can be indicative of various health ailments; one of which I am prone to.. So on top of my "doom" to my gloom..I am now f'n worried about my heart. I do happen to have a physical in 48 hours.
Translated to Thai: เขาบอกว่าเขาไม่เคยรู้สึกแบบนั้นมาก่อนฉันไปพักผ่อนและ .. ทริกเกอร์ไปข้างหน้าถ้าคุณเป็นคน hypocondriac อย่างฉัน: ฉันตัดสินใจที่จะค้นหา "ความรู้สึกของการลงโทษ" ด้วยความหวังว่าอาจจะถูกดูดเข้าไปในหลุมกระต่าย การสมรู้ร่วมคิดที่น่า

In [2]:
import pandas as pd

# โหลดข้อมูลจากไฟล์ CSV
df01 = pd.read_csv('dataset/dataset.csv')
df02 = pd.read_csv('dataset/dataset_augmented1.csv')

# ตรวจสอบข้อมูลเบื้องต้น
print(df01['label'].value_counts())
print(df02['label'].value_counts())

label
minimum     2587
moderate     394
mild         290
severe       282
Name: count, dtype: int64
label
minimum     2587
moderate     788
mild         580
severe       564
Name: count, dtype: int64


Data Augmentation( Contextual Augmentation(GPT-2))

In [21]:
import pandas as pd
import random
from transformers import GPT2Tokenizer, GPT2LMHeadModel
import torch

# ✅ โหลดโมเดลและ tokenizer
tokenizer = GPT2Tokenizer.from_pretrained("gpt2")
model = GPT2LMHeadModel.from_pretrained("gpt2")

# ✅ โหลด Dataset
dataset_path = "dataset/dataset_augmented1.csv"  # แก้เป็นชื่อไฟล์ที่ถูกต้อง
print(f"⏳ Loading dataset from {dataset_path}...")
df = pd.read_csv(dataset_path)
print(f"✅ Dataset loaded! Total samples: {len(df)}\n")

# ✅ ดูจำนวนตัวอย่างของแต่ละคลาส
print("🔍 Class distribution BEFORE augmentation:")
class_counts = df["label"].value_counts()
print(class_counts, "\n")

# ✅ คำนวณจำนวนที่ต้องเพิ่มให้ทุกคลาสมีขนาดเท่ากัน
target_count = class_counts.max()
labels_to_augment = class_counts[class_counts < target_count].index

# ✅ ฟังก์ชัน Generate ข้อความใหม่
def generate_text(prompt):
    """ ใช้ GPT-2 generate ข้อความใหม่จากตัวอย่างเดิม โดยคงความยาวใกล้เคียงต้นฉบับ """
    orig_length = len(prompt.split())
    target_length = orig_length + random.randint(-5, 5)
    
    print(f"🚀 Generating text from: {prompt[:50]}...")  # Print context ที่ใช้
    input_ids = tokenizer.encode(prompt, return_tensors="pt")
    
    # ปรับ max_new_tokens ให้เหมาะสมแทน max_length
    max_new_tokens = max(10, target_length - input_ids.shape[1])
    
    output = model.generate(
        input_ids,
        max_new_tokens=max_new_tokens,  # ใช้ max_new_tokens แทน
        num_return_sequences=1,
        do_sample=True,
        top_k=50,  # ลดความซ้ำของ output
        top_p=0.95  # เพิ่มความหลากหลายของ output
    )
    generated_text = tokenizer.decode(output[0], skip_special_tokens=True)
    
    # ตัดแต่งข้อความให้ใกล้เคียงความยาวต้นฉบับ
    generated_words = generated_text.split()
    generated_text = " ".join(generated_words[:orig_length])
    print(f"📝 Generated: {generated_text}\n")
    return generated_text

# ✅ สร้างตัวอย่างใหม่สำหรับ class ที่มีน้อย
new_samples = []
for label in labels_to_augment:
    existing_texts = df[df["label"] == label]["text"].tolist()
    num_samples_needed = target_count - class_counts[label]
    
    print(f"\n📝 Augmenting {num_samples_needed} samples for label: {label}")

    for _ in range(num_samples_needed):
        seed_text = random.choice(existing_texts)
        new_text = generate_text(seed_text)
        new_samples.append({"text": new_text, "label": label})

# ✅ รวม Dataset ใหม่
df_augmented = pd.concat([df, pd.DataFrame(new_samples)], ignore_index=True)

# ✅ ตรวจสอบ Class Distribution หลัง Augmentation
print("\n✅ Class distribution AFTER augmentation:")
print(df_augmented["label"].value_counts(), "\n")

# ✅ บันทึก Dataset ใหม่
output_path = "dataset_augmented.csv"
df_augmented.to_csv(output_path, index=False)
print(f"📂 Dataset saved as {output_path} with total samples: {len(df_augmented)}")


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


⏳ Loading dataset from dataset/dataset_augmented1.csv...
✅ Dataset loaded! Total samples: 4519

🔍 Class distribution BEFORE augmentation:
label
minimum     2587
moderate     788
mild         580
severe       564
Name: count, dtype: int64 


📝 Augmenting 1799 samples for label: moderate
🚀 Generating text from: So earlier today I was suffering from extreme dere...


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


📝 Generated: So earlier today I was suffering from extreme derealization, depression, and anxiety. So what I did is I let the thoughts free and whenever I got a tnhoguht I ignored it and I think I just suppressed my anxiety deep down. Now instead of having a panic attack I'm having body symptoms of it. I can't think myself form the symptoms. I can't find the trigger it just happened.

🚀 Generating text from: I do not get paid until next Tuesday and i am terr...


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


...

📝 Generated: Where each person does what they do because they love the other person and get pleasure out of pleasing their partner. And I know this sounds so horrible and I hate myself for it, but I almost feel like it will never happen. Like she's been broken. Even if you put the pieces back together for a broken glass, it will never truly be like new. And I feel awful for feeling that way but I've been trying (and patiently waiting) for nearly a year now.

🚀 Generating text from: When I was 16 my braces were removed due to bone l...


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


📝 Generated: When I was 16 my braces were removed due to bone loss caused by Pre-juvenile periodontitis. My orthodontist had advised against a retainer because of cost and not believing I would need it. So sometime around my 17th year my teeth began to shift, horribly. Now I'm left with a horribly crooked and hanging front tooth, and have been terrified to speak to, or smile at anyone for years. It's absolutely destroyed my self esteem, and I've contemplated suicide many times because of it.

🚀 Generating text from: Every time I tell him to leave he threatens to har...


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


📝 Generated: Every time I tell him to leave he threatens to harm my pets or take them and release them to the wild (I have ferrets.... they CANNOT survive in the wild where I live) or he goes into rants about how useless I am and how I couldn't survive without him and somehow he worms his way back in for fear he might be right. TLDR; need him out. He threatens animals. **REALLY** don't wanna involve police. What do I do?

🚀 Generating text from: Eat good intestine bacteria probiotics, helping to...
📝 Generated: Eat good intestine bacteria probiotics, helping to increase the production of serotonin. Try and learn about meditation. I think it's not my scene. But I have an app called Headspace and it can help surprisingly &#x200b; I am almost killing myself 3 times.


✅ Class distribution AFTER augmentation:
label
mild        2587
minimum     2587
moderate    2587
severe      2587
Name: count, dtype: int64 

📂 Dataset saved as dataset_augmented.csv with total samples: 10348


In [2]:
import pandas as pd

# โหลดข้อมูลจากไฟล์ CSV
df01 = pd.read_csv('dataset/dataset.csv')
df02 = pd.read_csv('dataset/dataset_augmented1.csv')
df03 = pd.read_csv('dataset/dataset_augmented2.csv')

# ตรวจสอบข้อมูลเบื้องต้น
print(df01['label'].value_counts())
print(df02['label'].value_counts())
print(df03['label'].value_counts())

label
minimum     2587
moderate     394
mild         290
severe       282
Name: count, dtype: int64
label
minimum     2587
moderate     788
mild         580
severe       564
Name: count, dtype: int64
label
mild        2587
minimum     2587
moderate    2587
severe      2587
Name: count, dtype: int64
